## importy

In [1]:
from gensim.utils import tokenize
import numpy as np
import torch
from tqdm.notebook import tqdm

/media/kuba/ssdsam/anaconda3/lib/python3.8/site-packages/gensim/similarities/__init__.py:15: UserWarning: The gensim.similarities.levenshtein submodule is disabled, because the optional Levenshtein package <https://pypi.org/project/python-Levenshtein/> is unavailable. Install Levenhstein (e.g. `pip install python-Levenshtein`) to suppress this warning.
  warnings.warn(msg)


https://www.jmlr.org/papers/volume3/bengio03a/bengio03a.pdf

In [2]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
#device = 'cpu'

In [3]:
print('Using {} device'.format(device))

Using cuda device


In [4]:
device

device(type='cuda')

## przygotowanie zbiorów

In [5]:
pan_tadeusz_path_train= '/home/kuba/Syncthing/przedmioty/2020-02/ISI/zajecia9_ngramowy_model_jDDezykowy/pan-tadeusz-train.txt'

In [6]:
corpora_train = open(pan_tadeusz_path_train).read()

In [7]:
corpora_train_tokenized = list(tokenize(corpora_train,lowercase = True))

In [8]:
vocab_itos = sorted(set(corpora_train_tokenized))

In [9]:
len(vocab_itos)

16598

In [10]:
vocab_itos = vocab_itos[:15005]
vocab_itos[15001] = "<UNK>"
vocab_itos[15002] = "<BOS>"
vocab_itos[15003] = "<EOS>"
vocab_itos[15004] = "<PAD>"

In [11]:
len(vocab_itos)

15005

In [12]:
vocab_stoi = dict()
for i, token in enumerate(vocab_itos):
    vocab_stoi[token] = i

In [13]:
NGRAMS = 4

In [14]:
def get_token_id(dataset):
    token_ids = [vocab_stoi['<PAD>']] * (NGRAMS-1) + [vocab_stoi['<BOS>']]
    for token in dataset:
        try:
            token_ids.append(vocab_stoi[token])
        except KeyError:
            token_ids.append(vocab_stoi['<UNK>'])
    token_ids.append(vocab_stoi['<EOS>'])
    return token_ids

In [15]:
train_ids = get_token_id(corpora_train_tokenized)

In [16]:
train_ids[:30]

[15004,
 15004,
 15004,
 15002,
 7,
 5002,
 7247,
 11955,
 1432,
 7018,
 14739,
 5506,
 4696,
 4276,
 7505,
 2642,
 8477,
 7259,
 10870,
 10530,
 7506,
 12968,
 7997,
 1911,
 12479,
 11129,
 13069,
 11797,
 5819,
 6268]

In [17]:
def get_samples(dataset):
    samples = []
    for i in range(len(dataset)-NGRAMS):
        samples.append(dataset[i:i+NGRAMS])
    return samples

In [18]:
train_ids = get_samples(train_ids)

In [19]:
train_ids = torch.tensor(train_ids, device = device)

In [20]:
train_ids[:30]

tensor([[15004, 15004, 15004, 15002],
        [15004, 15004, 15002,     7],
        [15004, 15002,     7,  5002],
        [15002,     7,  5002,  7247],
        [    7,  5002,  7247, 11955],
        [ 5002,  7247, 11955,  1432],
        [ 7247, 11955,  1432,  7018],
        [11955,  1432,  7018, 14739],
        [ 1432,  7018, 14739,  5506],
        [ 7018, 14739,  5506,  4696],
        [14739,  5506,  4696,  4276],
        [ 5506,  4696,  4276,  7505],
        [ 4696,  4276,  7505,  2642],
        [ 4276,  7505,  2642,  8477],
        [ 7505,  2642,  8477,  7259],
        [ 2642,  8477,  7259, 10870],
        [ 8477,  7259, 10870, 10530],
        [ 7259, 10870, 10530,  7506],
        [10870, 10530,  7506, 12968],
        [10530,  7506, 12968,  7997],
        [ 7506, 12968,  7997,  1911],
        [12968,  7997,  1911, 12479],
        [ 7997,  1911, 12479, 11129],
        [ 1911, 12479, 11129, 13069],
        [12479, 11129, 13069, 11797],
        [11129, 13069, 11797,  5819],
        [130

## model

In [21]:
class NeuralLM(torch.nn.Module):

    def __init__(self):
        super(NeuralLM, self).__init__()
        self.emb = torch.nn.Embedding(len(vocab_itos),200)
        self.fc1 = torch.nn.Linear( (NGRAMS - 1 ) * 200,len(vocab_itos))        

    def forward(self, x):
        x = self.emb(x)
        x = x.reshape(-1, (NGRAMS-1)*200)
        x = self.fc1(x)
        return x

In [22]:
lm = NeuralLM().to(device)

In [23]:
criterion = torch.nn.CrossEntropyLoss()

In [24]:
optimizer = torch.optim.Adam(lm.parameters())

In [25]:
BATCH_SIZE = 50
EPOCHS = 2

In [26]:
lm.train()
for epoch in range(EPOCHS):
    batches = 0
    loss_sum =0
    acc_score = 0

    for i in tqdm(range(0, len(train_ids)-BATCH_SIZE+1, BATCH_SIZE)):
        X = train_ids[i:i+BATCH_SIZE,:3]
        Y = train_ids[i:i+BATCH_SIZE,3]
        predictions = lm(X)
        loss = criterion(predictions,Y)
    
    
        
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        
        loss_sum += loss.item()
        batches += 1
        
        
        
        if i % 100 == 0:
            loss_current = loss_sum / batches
            print(f'updates: {i // BATCH_SIZE}/{len(train_ids) / BATCH_SIZE}',  end ='\t')
            print('loss: ', round(loss_current,5) , end = '\t')
            print(np.exp(loss_current))

updates: 0/1140.44	loss:  9.86444	19234.062158106106
updates: 2/1140.44	loss:  9.8484	18928.01779784466
updates: 4/1140.44	loss:  9.80547	18132.650966417892
updates: 6/1140.44	loss:  9.79965	18027.479440297415
updates: 8/1140.44	loss:  9.77038	17507.36347175203
updates: 10/1140.44	loss:  9.76398	17395.75469455178
updates: 12/1140.44	loss:  9.73982	16980.495266286664
updates: 14/1140.44	loss:  9.72326	16701.657281817905
updates: 16/1140.44	loss:  9.69892	16299.98679638986
updates: 18/1140.44	loss:  9.68147	16018.075454520396
updates: 20/1140.44	loss:  9.66146	15700.642679967945
updates: 22/1140.44	loss:  9.64514	15446.55612236878
updates: 24/1140.44	loss:  9.63481	15287.844411692564
updates: 26/1140.44	loss:  9.61562	14997.145144959657
updates: 28/1140.44	loss:  9.59612	14707.667295823418
updates: 30/1140.44	loss:  9.59734	14725.558518710543
updates: 32/1140.44	loss:  9.57319	14374.268338397032
updates: 34/1140.44	loss:  9.57122	14345.899296320918
updates: 36/1140.44	loss:  9.56701	1428

updates: 330/1140.44	loss:  9.11307	9073.127538588904
updates: 332/1140.44	loss:  9.11521	9092.55656620755
updates: 334/1140.44	loss:  9.11411	9082.506276953594
updates: 336/1140.44	loss:  9.11571	9097.134109738194
updates: 338/1140.44	loss:  9.11643	9103.684259568952
updates: 340/1140.44	loss:  9.11472	9088.128314022937
updates: 342/1140.44	loss:  9.11445	9085.648108887002
updates: 344/1140.44	loss:  9.11275	9070.196598788874
updates: 346/1140.44	loss:  9.11072	9051.816586981453
updates: 348/1140.44	loss:  9.10746	9022.324096148663
updates: 350/1140.44	loss:  9.09881	8944.644785746445
updates: 352/1140.44	loss:  9.0974	8932.002982678183
updates: 354/1140.44	loss:  9.09248	8888.200263524552
updates: 356/1140.44	loss:  9.09368	8898.855668455715
updates: 358/1140.44	loss:  9.09367	8898.789644671228
updates: 360/1140.44	loss:  9.09273	8890.413009589885
updates: 362/1140.44	loss:  9.09339	8896.294440774267
updates: 364/1140.44	loss:  9.09519	8912.316074222827
updates: 366/1140.44	loss:  9.

updates: 666/1140.44	loss:  8.99364	8051.727595812018
updates: 668/1140.44	loss:  8.99451	8058.6848486262925
updates: 670/1140.44	loss:  8.99405	8055.021602502067
updates: 672/1140.44	loss:  8.99419	8056.105948832661
updates: 674/1140.44	loss:  8.99388	8053.611608336102
updates: 676/1140.44	loss:  8.99369	8052.094117881097
updates: 678/1140.44	loss:  8.99224	8040.458152382287
updates: 680/1140.44	loss:  8.99194	8038.053335002441
updates: 682/1140.44	loss:  8.99141	8033.74830832689
updates: 684/1140.44	loss:  8.99209	8039.207644204204
updates: 686/1140.44	loss:  8.99282	8045.106282708816
updates: 688/1140.44	loss:  8.99282	8045.111940490653
updates: 690/1140.44	loss:  8.99322	8048.354424117917
updates: 692/1140.44	loss:  8.99375	8052.572291234546
updates: 694/1140.44	loss:  8.99274	8044.494845967595
updates: 696/1140.44	loss:  8.99331	8049.071159556381
updates: 698/1140.44	loss:  8.99081	8028.964131562491
updates: 700/1140.44	loss:  8.99127	8032.6636958293075
updates: 702/1140.44	loss: 

updates: 1002/1140.44	loss:  8.94898	7700.036144682901
updates: 1004/1140.44	loss:  8.95002	7708.070308864663
updates: 1006/1140.44	loss:  8.95076	7713.746500033021
updates: 1008/1140.44	loss:  8.95178	7721.589750170172
updates: 1010/1140.44	loss:  8.95239	7726.314794093976
updates: 1012/1140.44	loss:  8.95248	7727.001743843481
updates: 1014/1140.44	loss:  8.95125	7717.554998534523
updates: 1016/1140.44	loss:  8.95245	7726.771794653452
updates: 1018/1140.44	loss:  8.95343	7734.361554381286
updates: 1020/1140.44	loss:  8.95281	7729.597111874374
updates: 1022/1140.44	loss:  8.95345	7734.552456172466
updates: 1024/1140.44	loss:  8.95393	7738.231207628671
updates: 1026/1140.44	loss:  8.9532	7732.616378307852
updates: 1028/1140.44	loss:  8.95325	7733.018758238669
updates: 1030/1140.44	loss:  8.95164	7720.556926368948
updates: 1032/1140.44	loss:  8.95086	7714.549583754533
updates: 1034/1140.44	loss:  8.94979	7706.241743498811
updates: 1036/1140.44	loss:  8.94927	7702.301058775793
updates: 10

updates: 0/1140.44	loss:  6.15737	472.1866640173176
updates: 2/1140.44	loss:  6.49404	661.187925979436
updates: 4/1140.44	loss:  6.65829	779.2170420167108
updates: 6/1140.44	loss:  6.62956	757.1489470634459
updates: 8/1140.44	loss:  6.65585	777.3152225941299
updates: 10/1140.44	loss:  6.67206	790.0180958432777
updates: 12/1140.44	loss:  6.63402	760.5324281009048
updates: 14/1140.44	loss:  6.68404	799.5459559090896
updates: 16/1140.44	loss:  6.61777	748.2778980564127
updates: 18/1140.44	loss:  6.57939	720.0980719875246
updates: 20/1140.44	loss:  6.51658	676.2620199169293
updates: 22/1140.44	loss:  6.46151	640.0248403780723
updates: 24/1140.44	loss:  6.46224	640.494371451859
updates: 26/1140.44	loss:  6.43054	620.5063001785295
updates: 28/1140.44	loss:  6.40764	606.4634738269821
updates: 30/1140.44	loss:  6.41106	608.5407457017043
updates: 32/1140.44	loss:  6.38026	590.0824163849289
updates: 34/1140.44	loss:  6.39267	597.4521930632917
updates: 36/1140.44	loss:  6.37786	588.665120539213
u

updates: 332/1140.44	loss:  5.47759	239.26826156457057
updates: 334/1140.44	loss:  5.47425	238.47132434042138
updates: 336/1140.44	loss:  5.47124	237.75381036089195
updates: 338/1140.44	loss:  5.46828	237.0514708229553
updates: 340/1140.44	loss:  5.46633	236.59107588196017
updates: 342/1140.44	loss:  5.46323	235.85918885196514
updates: 344/1140.44	loss:  5.45979	235.0481202501975
updates: 346/1140.44	loss:  5.45482	233.88276728733683
updates: 348/1140.44	loss:  5.45129	233.05750880340034
updates: 350/1140.44	loss:  5.44064	230.59063053924396
updates: 352/1140.44	loss:  5.43762	229.89499424574507
updates: 354/1140.44	loss:  5.43238	228.69365939854498
updates: 356/1140.44	loss:  5.43083	228.33822474373926
updates: 358/1140.44	loss:  5.42814	227.72580915545606
updates: 360/1140.44	loss:  5.42688	227.43841499756414
updates: 362/1140.44	loss:  5.42288	226.5301297628514
updates: 364/1140.44	loss:  5.41899	225.65009437116206
updates: 366/1140.44	loss:  5.41739	225.29117644466837
updates: 368/

updates: 668/1140.44	loss:  5.08035	160.8303843062857
updates: 670/1140.44	loss:  5.07962	160.71266685347777
updates: 672/1140.44	loss:  5.07849	160.53077894316107
updates: 674/1140.44	loss:  5.0772	160.32454480905386
updates: 676/1140.44	loss:  5.07498	159.96868295986656
updates: 678/1140.44	loss:  5.07317	159.67927840044993
updates: 680/1140.44	loss:  5.07184	159.46688719152698
updates: 682/1140.44	loss:  5.06961	159.1128510694478
updates: 684/1140.44	loss:  5.06725	158.73788880465125
updates: 686/1140.44	loss:  5.06451	158.30269174571254
updates: 688/1140.44	loss:  5.06235	157.96098967621054
updates: 690/1140.44	loss:  5.06079	157.71571287983164
updates: 692/1140.44	loss:  5.05792	157.26378561246895
updates: 694/1140.44	loss:  5.05509	156.81901538312877
updates: 696/1140.44	loss:  5.05214	156.3570371113183
updates: 698/1140.44	loss:  5.05113	156.1993894696543
updates: 700/1140.44	loss:  5.04873	155.8249690999114
updates: 702/1140.44	loss:  5.04718	155.5831647396487
updates: 704/1140

updates: 1006/1140.44	loss:  4.87329	130.75092553694728
updates: 1008/1140.44	loss:  4.87267	130.66971440876225
updates: 1010/1140.44	loss:  4.87085	130.43130800560004
updates: 1012/1140.44	loss:  4.86962	130.27148542684589
updates: 1014/1140.44	loss:  4.86827	130.09519435102845
updates: 1016/1140.44	loss:  4.86702	129.93340453801687
updates: 1018/1140.44	loss:  4.86637	129.8480674565626
updates: 1020/1140.44	loss:  4.86515	129.69023051144623
updates: 1022/1140.44	loss:  4.86318	129.4356906505186
updates: 1024/1140.44	loss:  4.86209	129.29402291855033
updates: 1026/1140.44	loss:  4.86096	129.1487131766509
updates: 1028/1140.44	loss:  4.85994	129.01682401556738
updates: 1030/1140.44	loss:  4.85924	128.92603097761628
updates: 1032/1140.44	loss:  4.85834	128.81061582186257
updates: 1034/1140.44	loss:  4.85806	128.7737779615554
updates: 1036/1140.44	loss:  4.85808	128.77709147187798
updates: 1038/1140.44	loss:  4.85683	128.6156449527718
updates: 1040/1140.44	loss:  4.85576	128.477674364517

## ewaluacja

### zadanie:

- wczytać zbiór testowy
- napisać funkcję liczącą perplexity dla dowolnego zbioru i policzyć perplexity dla zbioru testowego

In [35]:
get_ppl(test_ids)

updates: 0/1140.44	loss:  7.93691	2798.69023798398
updates: 20/1140.44	loss:  7.2917	1468.0696196794395
updates: 40/1140.44	loss:  7.02505	1124.4520230095873
updates: 60/1140.44	loss:  7.02153	1120.498903823149
updates: 80/1140.44	loss:  6.97483	1069.377989926981
updates: 100/1140.44	loss:  7.01626	1114.614360205092
updates: 120/1140.44	loss:  7.01344	1111.4692099745646
updates: 140/1140.44	loss:  7.02334	1122.5331375146593
updates: 160/1140.44	loss:  7.02724	1126.9124589152598
updates: 180/1140.44	loss:  7.047	1149.409103844335
updates: 200/1140.44	loss:  7.05975	1164.1482767554144
updates: 220/1140.44	loss:  7.06818	1174.0069599198582



1174.0069599198582

## parametry modelu

In [36]:
list(lm.parameters())

[Parameter containing:
 tensor([[ 1.2962,  2.2548, -0.5289,  ...,  0.7910,  0.3451,  3.1669],
         [ 0.6231, -1.0074,  0.4776,  ...,  1.1894,  1.4892,  1.0638],
         [ 0.6153,  0.2596, -1.9959,  ..., -0.5816,  0.6102,  1.2497],
         ...,
         [ 3.6131, -1.3489, -0.8311,  ...,  0.9109,  2.3637, -0.5194],
         [ 0.1942,  0.9902, -0.4598,  ...,  0.5558,  0.7963, -0.0882],
         [ 0.1043,  1.7519, -0.5018,  ..., -0.0734,  0.5121, -1.0132]],
        device='cuda:0', requires_grad=True),
 Parameter containing:
 tensor([[ 0.0084, -0.0304, -0.0707,  ...,  0.0578, -0.0801, -0.0080],
         [-0.1369, -0.1782,  0.2099,  ..., -0.0111, -0.0396, -0.1987],
         [-0.0470, -0.0926,  0.0525,  ..., -0.0092,  0.0290, -0.0435],
         ...,
         [-0.0967,  0.0055,  0.0719,  ..., -0.0688,  0.0067, -0.0878],
         [-0.1023, -0.1981,  0.1966,  ..., -0.0676, -0.0961, -0.1946],
         [-0.1015, -0.1989,  0.1953,  ..., -0.0674, -0.0961, -0.1947]],
        device='cuda:0', r

In [37]:
list(lm.parameters())[0].shape

torch.Size([15005, 200])

In [38]:
list(lm.parameters())[1].shape

torch.Size([15005, 600])

In [39]:
list(lm.parameters())[2].shape

torch.Size([15005])

## Inferencja

In [40]:
'Gości innych nie widział oprócz spółleśników'

'Gości innych nie widział oprócz spółleśników'

In [41]:
tokenized = list(tokenize('Gości innych nie widział oprócz spółleśników',lowercase = True))

In [42]:
tokenized = tokenized[-NGRAMS  :-1 ]

In [43]:
tokenized

['nie', 'widział', 'oprócz']

In [44]:
ids = []
for word in tokenized:
    if word in vocab_stoi:
        ids.append(vocab_stoi[word])
    else:
        ids.append(vocab_stoi['<UNK>'])

In [45]:
ids

[5873, 13240, 6938]

In [46]:
lm.eval()

NeuralLM(
  (emb): Embedding(15005, 200)
  (fc1): Linear(in_features=600, out_features=15005, bias=True)
)

In [47]:
ids = torch.tensor(ids, dtype = torch.long, device = device)

In [48]:
ids

tensor([ 5873, 13240,  6938], device='cuda:0')

In [49]:
preds= lm(torch.tensor(ids, dtype = torch.long))

<ipython-input-49-cbeeab1035ab>:1: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  preds= lm(torch.tensor(ids, dtype = torch.long))


In [50]:
torch.argmax(torch.softmax(preds,1),1).item()

10861

In [51]:
torch.max(torch.softmax(preds,1),1)

torch.return_types.max(
values=tensor([0.2408], device='cuda:0', grad_fn=<MaxBackward0>),
indices=tensor([10861], device='cuda:0'))

In [52]:
vocab_itos[torch.argmax(torch.softmax(preds,1),1).item()]

'sposobu'